# DAtaset from benedix et al, obtained from mCS-AB dataset.
all experimental values need to be mutiply by -1 

In [1]:
import pandas as pd
import prody
import seaborn as sns
import matplotlib.pyplot as plt
#import xgboost as xgb
from pathlib import Path
import pickle
from runpy import run_path
import numpy as np
from sklearn.externals import joblib
from biopandas.pdb import PandasPdb
from sklearn.metrics import mean_squared_error,mean_absolute_error,r2_score

from multiprocessing import Pool
import time
import math
import os
import sys

ABPRED_DIR = Path.cwd().parent
if ABPRED_DIR not in sys.path:
    sys.path.append(str(ABPRED_DIR))
from AbPred.FoldX import FoldX
from AbPred.FoldX import names_stability_complex_wt,names_stability_complex_mut
from AbPred.interface_contacts import InterfaceContacts
from AbPred.features_ic import ArpeggioFeatures
from features3D.Structural import run_pops
from features3D.Structural import POPS_parse2
%matplotlib inline

features15 = ['clash', 'covalent', 'vdw_clash', 'vdw', 'proximal', 'hbond',
       'weak_hbond', 'xbond', 'ionic', 'metal_complex', 'aromatic',
       'hydrophobic', 'carbonyl', 'polar', 'weak_polar']

/Users/vfica/Documents/GitHub/AbPred/AbPred/../libs/arpeggio


In [22]:
# Paths vih data
PDBS_DIR = Path("../benchmark/228_benedix/")
benedix_pdbs = list(PDBS_DIR.glob("*.pdb"))

In [23]:
benedix_pdbs

[PosixPath('../benchmark/228_benedix/1AHW.mut.36.Y157A.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.36.Y157A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.37.T167A.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.37.T167A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.38.T170A.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.38.T170A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.39.D178A.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.39.D178A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.40.T197A.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.40.T197A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.41.V198A.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.41.V198A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.42.H30A.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.42.H30A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.43.Y32A.pdb'),
 PosixPath('../be

### Parse only protein data  and write pdb

In [8]:
for pdb in benedix_pdbs:
    
    parser = prody.parsePDB(pdb)
    protein = parser.select("protein")
    prody.writePDB(str(pdb)[:-4]+".protein",protein)

@> 9825 atoms and 1 coordinate set(s) were parsed in 0.10s.
@> 9830 atoms and 1 coordinate set(s) were parsed in 0.09s.
@> 9830 atoms and 1 coordinate set(s) were parsed in 0.09s.
@> 9829 atoms and 1 coordinate set(s) were parsed in 0.10s.
@> 9830 atoms and 1 coordinate set(s) were parsed in 0.09s.
@> 9830 atoms and 1 coordinate set(s) were parsed in 0.09s.
@> 3493 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 3491 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 3491 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 3491 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 3489 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 3497 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 3495 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 3491 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 3496 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 3491 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 3489 atoms and 1 coordinate set(s) we

In [303]:
protein_pdbs = list(PDBS_DIR.glob("*protein.pdb"))

In [304]:
protein_pdbs

[PosixPath('../benchmark/228_benedix/1AHW.mut.36.Y157A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.37.T167A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.38.T170A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.39.D178A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.40.T197A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1AHW.mut.41.V198A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.42.H30A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.43.Y32A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.44.Y49A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.45.Y50A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.46.W92A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.47.S93A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.48.D100A.protein.pdb'),
 PosixPath('../benchmark/228_benedix/1DVF.mut.49.Y101A.protein.pdb'),
 PosixPath('../benchmark/2

# Repair PDBS

In [6]:

CWD = Path.cwd()


In [7]:
def main(pdb):
    
    
    foldx = FoldX(verbose=True)
    foldx.repair_pdb(pdb_file=pdb)

In [8]:
try:
    os.chdir(PDBS_DIR)
    with Pool(4) as p:
        print(p.map(main, [str(pdb.name) for pdb in protein_pdbs]))
        
finally:
    os.chdir(CWD)

foldx path exported
foldx path exported
foldx path exported
foldx path exported
   ********************************************
   ********************************************
   ********************************************
   ********************************************
   ***                                      ***
   ***                                      ***
   ***                                      ***
   ***                                      ***
   ***             FoldX 5 (c)              ***
   ***             FoldX 5 (c)              ***
   ***             FoldX 5 (c)              ***
   ***             FoldX 5 (c)              ***
   ***                                      ***
   ***                                      ***
   ***                                      ***
   ***                                      ***
   ***     code by the FoldX Consortium     ***
   ***     code by the FoldX Consortium     ***
   ***     code by the FoldX Consortium     ***
   ***  

partial covalent interactions = 0.00
Energy_Ionisation =             0.85
Energy_Ionisation =             0.85
Energy_Ionisation =             0.85
Entropy Complex =               0.00
Entropy Complex =               0.00
Entropy Complex =               0.00
-----------------------------------------------------------
-----------------------------------------------------------
-----------------------------------------------------------
Total          = 				  210.61
Total          = 				  212.37
Total          = 				  213.06



Now Optimizing Residues
Now Optimizing Residues
Now Optimizing Residues
Now optimizing Residue ASPA1
Now optimizing Residue ASPA1
Now optimizing Residue ASPA1
Optimize Residue ID= ASPA1
Optimize Residue ID= ASPA1
Optimize Residue ID= ASPA1



BackHbond       =               -266.42
BackHbond       =               -267.35
BackHbond       =               -266.36
SideHbond       =               -89.88
SideHbond       =               -88.29
SideHbond       =          

Energy_VdW      =               -542.51
Entropy Complex =               0.00
Electro         =               -22.24
Electro         =               -22.26
Electro         =               -22.57
Energy_SolvP    =               748.26
-----------------------------------------------------------
Energy_SolvP    =               749.37
Energy_SolvP    =               751.38
Energy_SolvH    =               -690.45
Total          = 				  1534.21
Energy_SolvH    =               -691.71
Energy_SolvH    =               -693.53
Energy_vdwclash =               77.70

Energy_vdwclash =               78.48
Energy_vdwclash =               78.72
Now Optimizing Residues
energy_torsion  =               50.40
energy_torsion  =               50.32
energy_torsion  =               50.47
backbone_vdwclash=              145.49
Now optimizing Residue ASPA1
backbone_vdwclash=              145.76
backbone_vdwclash=              146.73
Optimize Residue ID= ASPA1
Entropy_sidec   =               255.01
Entropy_sidec

backbone_vdwclash=              146.73
Optimize Residue ID= LYSA3
Entropy_sidec   =               255.01
Entropy_sidec   =               255.05
Entropy_sidec   =               255.36

Entropy_mainc   =               702.62
Entropy_mainc   =               703.28
Entropy_mainc   =               702.64
water bonds     =               0.00
BackHbond       =               -627.22
water bonds     =               0.00
water bonds     =               0.00
helix dipole    =               0.00
SideHbond       =               -207.12
helix dipole    =               0.00
helix dipole    =               0.00
loop_entropy    =               0.00
Energy_VdW      =               -1494.13
loop_entropy    =               0.00
loop_entropy    =               0.00
cis_bond        =               4.50
Electro         =               -41.04
cis_bond        =               4.50
cis_bond        =               4.50
disulfide       =               -17.23
Energy_SolvP    =               2108.69
disulfide       

cis_bond        =               4.50
Energy_SolvP    =               2108.60
cis_bond        =               4.50
kn electrostatic=               -1.55
disulfide       =               -17.23
Energy_SolvH    =               -1909.69
disulfide       =               -17.23
partial covalent interactions = 0.00
kn electrostatic=               -1.55
Energy_vdwclash =               612.97
kn electrostatic=               -1.56
Energy_Ionisation =             0.85
partial covalent interactions = 0.00
energy_torsion  =               297.26
partial covalent interactions = 0.00
Energy_Ionisation =             0.85
Entropy Complex =               0.00
backbone_vdwclash=              549.31
Energy_Ionisation =             0.85
Entropy Complex =               0.00
-----------------------------------------------------------
Entropy_sidec   =               706.70
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  210.91
Entropy_mainc 

...

Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  507.48

Residue TRPY62 has high Energy, we mutate it to itself
Repair Residue ID= TRPY62

BackHbond       =               -245.82
SideHbond       =               -171.74
Energy_VdW      =               -621.47
Electro         =               -17.06
Energy_SolvP    =               856.10
Energy_SolvH    =               -800.69
Energy_vdwclash =               142.26
energy_torsion  =               50.22
backbone_vdwclash=              398.69
Entropy_sidec   =               326.08
Entropy_mainc   =               1009.89
water bonds     =               0.00
helix dipole    =               0.00
loop_entropy    =               0.00
cis_bond        =               6.74
disulfide       =               -27.25
kn electrostatic=               -0.93
partial covalent interactions = 0.00
Energy_Ionisation =             1.14
Entropy Complex =               0.00
---------------------

Energy_SolvH    =               -800.28
Energy_vdwclash =               139.60
energy_torsion  =               50.12
backbone_vdwclash=              398.13
Entropy_sidec   =               325.92
Entropy_mainc   =               1009.81
water bonds     =               0.00
helix dipole    =               0.00
loop_entropy    =               0.00
cis_bond        =               6.74
disulfide       =               -27.25
kn electrostatic=               -0.92
partial covalent interactions = 0.00
Energy_Ionisation =             1.14
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  503.27

Residue LEUY75 has high Energy, we mutate it to itself
Residue ASNY77 has high Energy, we mutate it to itself
Repair Residue ID= ASNY77

BackHbond       =               -245.72
SideHbond       =               -172.81
Energy_VdW      =               -620.81
Electro         =               -17.05
Energy_SolvP    =               854.46
Ene

disulfide       =               -27.25
kn electrostatic=               -0.92
partial covalent interactions = 0.00
Energy_Ionisation =             1.14
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  499.09

Residue SERY91 has high Energy, we mutate it to itself
We optimize, instead of self-mutatingSERY91
Repair Residue ID= SERY91

BackHbond       =               -246.81
SideHbond       =               -173.91
Energy_VdW      =               -621.01
Electro         =               -17.05
Energy_SolvP    =               854.17
Energy_SolvH    =               -800.49
Energy_vdwclash =               137.66
energy_torsion  =               49.61
backbone_vdwclash=              398.07
Entropy_sidec   =               326.51
Entropy_mainc   =               1009.68
water bonds     =               0.00
helix dipole    =               0.00
loop_entropy    =               0.00
cis_bond        =               6.74
disulfide     

Repair Residue ID= ASNY106

BackHbond       =               -246.91
SideHbond       =               -174.04
Energy_VdW      =               -620.98
Electro         =               -17.17
Energy_SolvP    =               853.78
Energy_SolvH    =               -800.56
Energy_vdwclash =               136.36
energy_torsion  =               47.41
backbone_vdwclash=              398.32
Entropy_sidec   =               326.49
Entropy_mainc   =               1009.59
water bonds     =               0.00
helix dipole    =               0.00
loop_entropy    =               0.00
cis_bond        =               6.74
disulfide       =               -27.25
kn electrostatic=               -0.91
partial covalent interactions = 0.00
Energy_Ionisation =             1.14
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  493.67

Residue TRPY108 has high Energy, we mutate it to itself
Residue VALY109 has high Energy, we mutate it to itself


Entropy_mainc   =               1009.53
water bonds     =               0.00
helix dipole    =               0.00
loop_entropy    =               0.00
cis_bond        =               6.74
disulfide       =               -27.32
kn electrostatic=               -0.91
partial covalent interactions = 0.00
Energy_Ionisation =             1.14
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  489.81

Residue ASPY119 has high Energy, we mutate it to itself
Repair Residue ID= ASPY119

BackHbond       =               -248.00
SideHbond       =               -177.05
Energy_VdW      =               -620.71
Electro         =               -16.97
Energy_SolvP    =               852.13
Energy_SolvH    =               -800.17
Energy_vdwclash =               135.40
energy_torsion  =               47.24
backbone_vdwclash=              398.13
Entropy_sidec   =               327.05
Entropy_mainc   =               1009.54
water bonds     

### Wildtype repair

In [27]:
benedixwt_files = list(Path("../benchmark/benedix_wt/").glob("*.pdb"))


In [29]:
# get only protein 
for pdb in benedixwt_files:
    
    parser = prody.parsePDB(pdb)
    protein = parser.select("protein")
    prody.writePDB(str(pdb)[:-4]+".protein",protein)

@> 9830 atoms and 1 coordinate set(s) were parsed in 0.13s.
@> 3654 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 3465 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 3456 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4297 atoms and 1 coordinate set(s) were parsed in 0.06s.


In [30]:
protein_wt = list(Path("../benchmark/benedix_wt/").glob("*protein.pdb"))

In [65]:
protein_wt[3:4]

[PosixPath('../benchmark/benedix_wt/1VFB.protein.pdb')]

In [66]:
def main(pdb):
    
    foldx = FoldX(verbose=True)
    foldx.repair_pdb(pdb_file=pdb)
    
CWD = Path.cwd()


try:
    os.chdir(Path("../benchmark/benedix_wt/"))
    with Pool(4) as p:
        print(p.map(main, [str(pdb.name) for pdb in protein_wt[3:4]]))
        
finally:
    os.chdir(CWD)

foldx path exported
   ********************************************
   ***                                      ***
   ***             FoldX 5 (c)              ***
   ***                                      ***
   ***     code by the FoldX Consortium     ***
   ***                                      ***
   ***     Jesper Borg, Frederic Rousseau   ***
   ***    Joost Schymkowitz, Luis Serrano   ***
   ***    Peter Vanhee, Erik Verschueren    ***
   ***     Lies Baeten, Javier Delgado      ***
   ***       and Francois Stricher          ***
   *** and any other of the 9! permutations ***
   ***   based on an original concept by    ***
   ***   Raphael Guerois and Luis Serrano   ***
   ********************************************

Start RepairPDB >>>

1 models read: 1VFB.protein.pdb
"1VFB_Repair.fxout"
Repair will take all residues into account
wild type

BackHbond       =               -220.93
SideHbond       =               -77.79
Energy_VdW      =               -417.19
Electro      

SideHbond       =               -81.58
Energy_VdW      =               -417.06
Electro         =               -17.57
Energy_SolvP    =               578.04
Energy_SolvH    =               -527.45
Energy_vdwclash =               31.71
energy_torsion  =               8.47
backbone_vdwclash=              152.47
Entropy_sidec   =               203.12
Entropy_mainc   =               536.31
water bonds     =               0.00
helix dipole    =               -2.01
loop_entropy    =               0.00
cis_bond        =               2.25
disulfide       =               -20.19
kn electrostatic=               -0.50
partial covalent interactions = 0.00
Energy_Ionisation =             0.74
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  73.33

Now optimizing Residue LEUA11
Optimize Residue ID= LEUA11

BackHbond       =               -220.96
SideHbond       =               -81.58
Energy_VdW      =               -417.07
Electr


BackHbond       =               -220.92
SideHbond       =               -81.65
Energy_VdW      =               -417.01
Electro         =               -17.56
Energy_SolvP    =               577.81
Energy_SolvH    =               -527.49
Energy_vdwclash =               31.39
energy_torsion  =               8.44
backbone_vdwclash=              152.45
Entropy_sidec   =               203.15
Entropy_mainc   =               536.30
water bonds     =               0.00
helix dipole    =               -2.01
loop_entropy    =               0.00
cis_bond        =               2.25
disulfide       =               -20.19
kn electrostatic=               -0.50
partial covalent interactions = 0.00
Energy_Ionisation =             0.74
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  72.74

Now optimizing Residue SERA26
Optimize Residue ID= SERA26

BackHbond       =               -220.93
SideHbond       =               -81.65
Energ

Optimize Residue ID= LYSA42

BackHbond       =               -221.31
SideHbond       =               -82.10
Energy_VdW      =               -416.99
Electro         =               -17.57
Energy_SolvP    =               577.77
Energy_SolvH    =               -527.50
Energy_vdwclash =               30.96
energy_torsion  =               8.43
backbone_vdwclash=              152.45
Entropy_sidec   =               203.28
Entropy_mainc   =               536.35
water bonds     =               0.00
helix dipole    =               -2.01
loop_entropy    =               0.00
cis_bond        =               2.25
disulfide       =               -20.19
kn electrostatic=               -0.50
partial covalent interactions = 0.00
Energy_Ionisation =             0.74
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  71.62

Now optimizing Residue SERA43
Optimize Residue ID= SERA43

BackHbond       =               -221.31
SideHbond       


Now optimizing Residue PROA59
Optimize Residue ID= PROA59

BackHbond       =               -221.32
SideHbond       =               -82.18
Energy_VdW      =               -416.98
Electro         =               -17.57
Energy_SolvP    =               577.66
Energy_SolvH    =               -527.56
Energy_vdwclash =               30.96
energy_torsion  =               8.41
backbone_vdwclash=              152.44
Entropy_sidec   =               203.28
Entropy_mainc   =               536.35
water bonds     =               0.00
helix dipole    =               -2.01
loop_entropy    =               0.00
cis_bond        =               2.25
disulfide       =               -20.19
kn electrostatic=               -0.50
partial covalent interactions = 0.00
Energy_Ionisation =             0.74
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  71.33

Now optimizing Residue SERA60
Optimize Residue ID= SERA60

BackHbond       =        

...

water bonds     =               0.00
helix dipole    =               -3.17
loop_entropy    =               0.00
cis_bond        =               2.25
disulfide       =               -20.16
kn electrostatic=               -0.46
partial covalent interactions = 0.00
Energy_Ionisation =             0.69
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  -12.55

Residue ARGC61 has high Energy, we mutate it to itself
We optimize, instead of self-mutatingARGC61
Repair Residue ID= ARGC61

BackHbond       =               -239.67
SideHbond       =               -124.53
Energy_VdW      =               -415.41
Electro         =               -16.58
Energy_SolvP    =               555.11
Energy_SolvH    =               -531.23
Energy_vdwclash =               14.40
energy_torsion  =               9.21
backbone_vdwclash=              152.30
Entropy_sidec   =               217.52
Entropy_mainc   =               539.29
water bonds     

-----------------------------------------------------------
Total          = 				  -16.50

Residue ASNC74 has high Energy, we mutate it to itself
Repair Residue ID= ASNC74

BackHbond       =               -240.64
SideHbond       =               -126.88
Energy_VdW      =               -414.68
Electro         =               -16.70
Energy_SolvP    =               553.00
Energy_SolvH    =               -531.17
Energy_vdwclash =               14.52
energy_torsion  =               9.06
backbone_vdwclash=              151.96
Entropy_sidec   =               218.43
Entropy_mainc   =               539.35
water bonds     =               0.00
helix dipole    =               -3.17
loop_entropy    =               0.00
cis_bond        =               2.25
disulfide       =               -20.16
kn electrostatic=               -0.46
partial covalent interactions = 0.00
Energy_Ionisation =             0.69
Entropy Complex =               0.00
-----------------------------------------------------------


Entropy_sidec   =               219.18
Entropy_mainc   =               539.41
water bonds     =               0.00
helix dipole    =               -3.19
loop_entropy    =               0.00
cis_bond        =               2.25
disulfide       =               -20.16
kn electrostatic=               -0.46
partial covalent interactions = 0.00
Energy_Ionisation =             0.69
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  -18.94

Residue SERC91 has high Energy, we mutate it to itself
Repair Residue ID= SERC91

BackHbond       =               -242.05
SideHbond       =               -128.52
Energy_VdW      =               -415.21
Electro         =               -16.71
Energy_SolvP    =               553.18
Energy_SolvH    =               -531.92
Energy_vdwclash =               14.52
energy_torsion  =               8.94
backbone_vdwclash=              152.29
Entropy_sidec   =               219.25
Entropy_mainc   =    

Total          = 				  -21.66

Residue VALC109 has high Energy, we mutate it to itself
Repair Residue ID= VALC109

BackHbond       =               -243.06
SideHbond       =               -129.95
Energy_VdW      =               -415.18
Electro         =               -16.71
Energy_SolvP    =               552.70
Energy_SolvH    =               -532.05
Energy_vdwclash =               14.49
energy_torsion  =               8.98
backbone_vdwclash=              152.35
Entropy_sidec   =               220.15
Entropy_mainc   =               539.37
water bonds     =               0.00
helix dipole    =               -3.20
loop_entropy    =               0.00
cis_bond        =               2.25
disulfide       =               -20.16
kn electrostatic=               -0.46
partial covalent interactions = 0.00
Energy_Ionisation =             0.69
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  -22.14

Residue ARGC112 has high En

Energy_SolvH    =               -532.16
Energy_vdwclash =               14.67
energy_torsion  =               9.00
backbone_vdwclash=              153.03
Entropy_sidec   =               221.29
Entropy_mainc   =               539.23
water bonds     =               0.00
helix dipole    =               -3.23
loop_entropy    =               0.00
cis_bond        =               2.25
disulfide       =               -20.16
kn electrostatic=               -0.48
partial covalent interactions = 0.00
Energy_Ionisation =             0.69
Entropy Complex =               0.00
-----------------------------------------------------------
Total          = 				  -24.84

Residue ARGC128 has high Energy, we mutate it to itself
Repair Residue ID= ARGC128

BackHbond       =               -244.69
SideHbond       =               -132.58
Energy_VdW      =               -415.47
Electro         =               -16.98
Energy_SolvP    =               553.58
Energy_SolvH    =               -532.20
Energy_vdwclash = 

In [4]:
repairedWT_pdbs = list(Path("../benchmark/benedix_wt/").glob("*Repair.pdb"))

In [5]:
repairedWT_pdbs

[PosixPath('../benchmark/benedix_wt/1AHW_Repair.pdb'),
 PosixPath('../benchmark/benedix_wt/1DVF_Repair.pdb'),
 PosixPath('../benchmark/benedix_wt/1JRH_Repair.pdb'),
 PosixPath('../benchmark/benedix_wt/1VFB_Repair.pdb'),
 PosixPath('../benchmark/benedix_wt/3HFM_Repair.pdb')]

## Read benedix csv and training database for exclude benedix pdb in training datbase


In [41]:
repaired_pdbs = list(PDBS_DIR.glob("*Repair.pdb"))

In [25]:
benedix_data = pd.read_csv("../data/blind_test_228mutations.csv",sep="\t")
benedix_data_original = benedix_data.loc[benedix_data["Mutation type"]=="Original"]
ab_bind = pd.read_csv("../data/ab_bind_dataset.csv",sep="\t")


In [26]:
benedix_data_original["pdb_mutation"] = benedix_data_original["PDB"].str.split(".",expand=True)[0]+"."+benedix_data_original["Mutation"]

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [27]:
ab_bind_mutations = ab_bind["#PDB"]+"."+ab_bind["Mutation"]
ab_bind["pdb_mutation"] = ab_bind_mutations

In [28]:
data_notin_modeldf = benedix_data_original.loc[~benedix_data_original["pdb_mutation"].isin(ab_bind_mutations)]


In [29]:
pdb_tobenchmark = list()
for pdb in repaired_pdbs:
    pdb = str(pdb)
    split_tomatch = pdb.split(".")[-3]
    if split_tomatch in data_notin_modeldf.index.map(str):
        pdb_tobenchmark.append(pdb)

In [30]:
data_notin_modeldf["partners"] = "nan"
data_notin_modeldf.partners.iloc[0:16] = "LH_I"
data_notin_modeldf.partners.iloc[16:23] = "AB_C"
data_notin_modeldf.partners.iloc[23:29] = "AB_C"
data_notin_modeldf.partners.iloc[29:34] = "AB_CD"
data_notin_modeldf.partners.iloc[34:] = "LH_Y"

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/pandas/core/indexing.py:189: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pan

In [31]:
import math
def deltaG_to_Kd(delg):
    Kd_value = math.exp((delg*1000)/(1.98*298.15))
    return Kd_value

def Kd_to_deltaG(Kd):
    if Kd > 0:
        deltaG = (math.log(Kd)*(1.98*298.15))/1000
        return deltaG
    else:
        deltaG = 0
        return deltaG

In [32]:
#Funcion para el sorting de paths por numero
def extract_num(pdb):
    return int(str(pdb).split(".")[-3])
def extract_num2(pdb):
    #for clean pdb
    return int(str(pdb).split(".")[-4])

pdb_tobenchmark.sort(key=extract_num)


In [33]:
data_notin_modeldf.loc['Experimental',:] = -data_notin_modeldf.Experimental

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


ddG = mutant - wildtype

# clean pdb

In [128]:
# clean pdb script
TOOLS_DIR = ABPRED_DIR/"libs/tools"
CLEANPDB = TOOLS_DIR / "clean_pdb.py"

def run_cleanpdb(filepath,pdb):
    sys.argv = ["",pdb]
    run_path(str(filepath),run_name="__main__")

In [129]:
# run clean pdb
for pdb in pdb_tobenchmark:
    run_cleanpdb(CLEANPDB,str(pdb))

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

...

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/home/vilion/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

In [305]:
clean_benchmark = list(PDBS_DIR.glob("*.clean.pdb"))
clean_benchmark.sort(key=extract_num2)

In [306]:
clean_benchmark

[PosixPath('../benchmark/228_benedix/1JRH.mut.0.E27A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.1.D28A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.2.Y30A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.3.K47A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.4.Y32A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.5.W53A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.6.D54A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.7.D56A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.8.Y99A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.9.N79A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.10.W82A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.11.R84A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.12.Y91A_Repair.clean.pdb'),
 PosixPath('../benchmark/228_benedix/1JRH.mut.13

# contact features

In [307]:
def main(i,pdbfile):
    pdb_number = str(pdbfile).split(".")[-4]
    partners_pdbs = data_notin_modeldf["partners"][int(pdb_number)]
    ic = InterfaceContacts(pdbfile)
    print("### Running arpeggio ###")
    ic.run_arpeggio()
    time.sleep(15)
    ic.get_ic(partners=partners_pdbs)
    print("Finish getting interface contact\n")
    #ic.get_pymol_contacts()
    print("### END ###\n")

In [139]:
with Pool(4) as p:
    print(p.starmap(main, enumerate(clean_benchmark)))

### Running arpeggio ###
### Running arpeggio ###
### Running arpeggio ###
### Running arpeggio ###
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting only interface contacts
Getting only interface contacts
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Finish getting interface contact

### END ###

Finish getting interface contact

### Running arpeggio ###
### END ###

### Running arpeggio ###
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting only interface contacts
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Finish getting interface contact

Getting only interface contacts
### END ###

### Running arpeggio ###
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting only interface contacts
Finish getting interface contact

##

In [308]:
ic_files = list(PDBS_DIR.glob("*.interface_contacts"))

In [309]:
ic_files.sort(key=extract_num2)

In [310]:
features = np.empty((len(clean_benchmark),15))
for i,(ic,pdb) in enumerate(zip(ic_files,clean_benchmark)):
    print(ic,pdb)
    ic_features = ArpeggioFeatures(level_sift="normal")
    ic_features.parse_contactdata(icfile=ic)
    ic_features.parse_pdbdata(pdbfile=pdb)
    
    contacts = ic_features.get_features()
    
    
    features[i] = contacts

../benchmark/228_benedix/1JRH.mut.0.E27A_Repair.clean.interface_contacts ../benchmark/228_benedix/1JRH.mut.0.E27A_Repair.clean.pdb
../benchmark/228_benedix/1JRH.mut.1.D28A_Repair.clean.interface_contacts ../benchmark/228_benedix/1JRH.mut.1.D28A_Repair.clean.pdb
../benchmark/228_benedix/1JRH.mut.2.Y30A_Repair.clean.interface_contacts ../benchmark/228_benedix/1JRH.mut.2.Y30A_Repair.clean.pdb
../benchmark/228_benedix/1JRH.mut.3.K47A_Repair.clean.interface_contacts ../benchmark/228_benedix/1JRH.mut.3.K47A_Repair.clean.pdb
../benchmark/228_benedix/1JRH.mut.4.Y32A_Repair.clean.interface_contacts ../benchmark/228_benedix/1JRH.mut.4.Y32A_Repair.clean.pdb
../benchmark/228_benedix/1JRH.mut.5.W53A_Repair.clean.interface_contacts ../benchmark/228_benedix/1JRH.mut.5.W53A_Repair.clean.pdb
../benchmark/228_benedix/1JRH.mut.6.D54A_Repair.clean.interface_contacts ../benchmark/228_benedix/1JRH.mut.6.D54A_Repair.clean.pdb
../benchmark/228_benedix/1JRH.mut.7.D56A_Repair.clean.interface_contacts ../benchma

In [315]:
contact_data = pd.DataFrame(features, index=[pdb.name for pdb in clean_benchmark],columns=features15)

In [317]:
contact_data.to_csv("benedix_contact15_data.csv")

# energy features
### Mutant

In [152]:
energetic_features = np.empty((len(clean_benchmark),29))

try:
    os.chdir(PDBS_DIR)
    
    for i,pdb in enumerate(clean_benchmark):
        pdb_number = str(pdb).split(".")[-4]
        partners_pdbs = data_notin_modeldf["partners"][int(pdb_number)]
        foldx = FoldX(verbose=False)
        result_analyse = foldx.analyse_complex(pdb_file=pdb.name, partners=partners_pdbs)
        energetic_features[i] = result_analyse
finally:
    os.chdir(CWD)

foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin 

In [160]:
energetic_data = pd.DataFrame(energetic_features, index=[pdb.name for pdb in clean_benchmark],columns=names_stability_complex_mut)

In [26]:
energetic_data.to_csv("benedix_energeticWT_data.csv")

NameError: name 'energetic_data' is not defined

### energetic WT

In [81]:
pdbWT_partner = (data_notin_modeldf.sort_values("PDB")["PDB"]+"/"+data_notin_modeldf.sort_values("PDB")["partners"]).unique()

In [83]:
pdbWT_partner

array(['1AHW.pdb/AB_C', '1DVF.pdb/AB_CD', '1JRH.pdb/LH_I',
       '1VFB.pdb/AB_C', '3HFM.pdb/LH_Y'], dtype=object)

In [82]:
repairedWT_pdbs

[PosixPath('../benchmark/benedix_wt/1AHW_Repair.pdb'),
 PosixPath('../benchmark/benedix_wt/1DVF_Repair.pdb'),
 PosixPath('../benchmark/benedix_wt/1JRH_Repair.pdb'),
 PosixPath('../benchmark/benedix_wt/1VFB_Repair.pdb'),
 PosixPath('../benchmark/benedix_wt/3HFM_Repair.pdb')]

In [85]:
energetic_features_wt = np.empty((len(repairedWT_pdbs),29))

try:
    os.chdir(Path("../benchmark/benedix_wt/"))
    
    for i,pdb in enumerate(repairedWT_pdbs):
        partners_pdbs = pdbWT_partner[i].split("/")[1]
        foldx = FoldX(verbose=False)
        result_analyse = foldx.analyse_complex(pdb_file=pdb.name, partners=partners_pdbs)
        energetic_features_wt[i] = result_analyse
finally:
    os.chdir(CWD)

foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH


In [88]:
energetic_dataWT = pd.DataFrame(energetic_features_wt, index=[pdb.name for pdb in repairedWT_pdbs],columns=names_stability_complex_wt)

In [90]:
energetic_dataWT.to_csv("benedix_energeticWT_data.csv")

## Merge data energetic

In [318]:

DF_energetic_wt = pd.read_csv("benedix_energeticWT_data.csv",index_col=0)
DF_energetic_mut = pd.read_csv("benedix_energeticMUT_data.csv",index_col=0)

In [319]:
DF_energetic_mut.columns = names_stability_complex_mut
DF_energetic_wt.columns = names_stability_complex_wt

In [320]:
pdbmut_index_code = DF_energetic_mut.index.str.split(".",expand=True).get_level_values(0)
pdbmut_index_code

Index(['1JRH', '1JRH', '1JRH', '1JRH', '1JRH', '1JRH', '1JRH', '1JRH', '1JRH',
       '1JRH', '1JRH', '1JRH', '1JRH', '1JRH', '1JRH', '1JRH', '1VFB', '1VFB',
       '1VFB', '1VFB', '1VFB', '1VFB', '1VFB', '1AHW', '1AHW', '1AHW', '1AHW',
       '1AHW', '1AHW', '1DVF', '1DVF', '1DVF', '1DVF', '1DVF', '3HFM', '3HFM',
       '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM',
       '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM',
       '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM', '3HFM'],
      dtype='object')

In [321]:
# Set new index mutant dataframe
DF_energetic_mut['codes'] = pdbmut_index_code
DF_energetic_mut.reset_index(inplace=True)
DF_energetic_mut.set_index('codes',inplace=True)
# Set new index wt dataframe
DF_energetic_wt['codes'] = DF_energetic_wt.index.str[:-11]
DF_energetic_wt.reset_index(inplace=True)
DF_energetic_wt.set_index('codes',inplace=True)

In [119]:
# merge
DF_energetic_wt_mut = DF_energetic_mut.merge(DF_energetic_wt,on='codes')

In [121]:
def convert_features_to_differences(df, keep_mut=False):
    """Convert `_wt` and `_mut` columns into `_wt` and `_change` columns.
    Create a new set of features (ending in `_change`) that describe the difference between values
    of the wildtype (features ending in `_wt`) and mutant (features ending in `_mut`) features.
    If `keep_mut` is `False`, removes all mutant features (features ending in `_mut`).
    """
    column_list = []
    for column_name, column in df.iteritems():
        if ('_mut' in column_name and column_name.replace('_mut', '_wt') in df.columns and
                df[column_name].dtype != object):
            if keep_mut:
                column_list.append(column)
            new_column = column - df[column_name.replace('_mut', '_wt')]
            if 'secondary_structure' in column_name:
                new_column = new_column.apply(lambda x: 1 if x else 0)
            new_column.name = column_name.replace('_mut', '_change')
            column_list.append(new_column)
        else:
            column_list.append(column)
    new_df = pd.concat(column_list, axis=1)
    return new_df

In [246]:
DF_energetic_changes =  convert_features_to_differences(DF_energetic_wt_mut)

In [140]:
DF_energetic_changes.to_csv("benedix_energetic_change_data.csv")

# SASA features

In [8]:
def get_pdb_chain(pdb,partner,outdir):
    protein = prody.parsePDB(pdb,chain=partner)
    pdbwrited = prody.writePDB(str(outdir.resolve())+"/"+"%s_%s" % (pdb.name[:-4], partner), protein)
    print("writing %s_%s" % (pdb.name[:-4], partner))
    return pdbwrited

In [24]:
# MUtant interface sasas calculate as (TA + TB - T) / 2.0.
# When T=total sas complex, TA= total sasa partner A , TB=total sasa partner B.

outfolder = Path('popout')
if not outfolder.exists():
    outfolder.mkdir()
complexMUT_sasas = list()
partnerA_MUT_sasas = list()
partnerB_MUT_sasas = list()
for i,pdb in enumerate(clean_benchmark):
    
    pdb_number = str(pdb).split(".")[-4]
    pp = data_notin_modeldf["partners"][int(pdb_number)]
    
    # Calculate sasa for complex
    asa_data = run_pops(str(pdb.resolve()), outdir=outfolder, mode='total')
    pops_complex = POPS_parse2(asa_data, mode='total') 
    complexMUT_sasas.append(list(pops_complex.values()))
    
    # Calculate sasa for partner A
    pdbA = get_pdb_chain(pdb.resolve(),partner=pp.split("_")[0],outdir=outfolder)
    asa_data = run_pops(pdbA, outdir=outfolder, mode='total')
    pops_A = POPS_parse2(asa_data, mode='total') 
    partnerA_MUT_sasas.append(list(pops_A.values()))
    
    # Calculate sasa for partner B
    pdbB = get_pdb_chain(pdb.resolve(),partner=pp.split("_")[1],outdir=outfolder)
    asa_data = run_pops(pdbB, outdir=outfolder, mode='total')
    pops_B = POPS_parse2(asa_data, mode='total') 
    partnerB_MUT_sasas.append(list(pops_B.values()))

@> 2672 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 762 atoms and 1 coordinate set(s) were parsed in 0.01s.


writing 1JRH.mut.0.E27A_Repair.clean_LH
writing 1JRH.mut.0.E27A_Repair.clean_I


@> 2673 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 762 atoms and 1 coordinate set(s) were parsed in 0.01s.


writing 1JRH.mut.1.D28A_Repair.clean_LH
writing 1JRH.mut.1.D28A_Repair.clean_I


@> 2669 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 762 atoms and 1 coordinate set(s) were parsed in 0.01s.


...

writing 3HFM.mut.109.K96R_Repair.clean_LH
writing 3HFM.mut.109.K96R_Repair.clean_Y


@> 3295 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 1003 atoms and 1 coordinate set(s) were parsed in 0.02s.


writing 3HFM.mut.112.K97R_Repair.clean_LH
writing 3HFM.mut.112.K97R_Repair.clean_Y


@> 3295 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 998 atoms and 1 coordinate set(s) were parsed in 0.02s.


writing 3HFM.mut.113.I98A_Repair.clean_LH
writing 3HFM.mut.113.I98A_Repair.clean_Y


In [338]:
# To numpy arrays
complexMUT_sasas = np.asarray(complexMUT_sasas)
partnerA_MUT_sasas = np.asarray(partnerA_MUT_sasas)
partnerB_MUT_sasas = np.asarray(partnerB_MUT_sasas)

In [339]:
# Phil, Phob, Total , interface sasa
interface_asa_MUT = ((partnerA_MUT_sasas + partnerB_MUT_sasas) - complexMUT_sasas)/2

In [340]:
# Pandas dataframe
interface_asa_MUT_df = pd.DataFrame(interface_asa_MUT,columns=["if_phil","if_phob","if_total"],index=[pdb.name for pdb in clean_benchmark])

In [341]:
interface_asa_MUT_df["sasa_phil_mut"] = complexMUT_sasas.T[0]
interface_asa_MUT_df["sasa_phob_mut"] = complexMUT_sasas.T[1]
interface_asa_MUT_df["sasa_total_mut"] = complexMUT_sasas.T[2]


In [343]:
interface_asa_MUT_df.to_csv("benedix_sasa_mut.v2.csv")

### sasa wildtype


In [10]:

outfolder = Path('popout')
if not outfolder.exists():
    outfolder.mkdir()
complexWT_sasas = list()
for pdb in repairedWT_pdbs:
        
    # Calculate sasa for complex
    asa_data = run_pops(str(pdb.resolve()), outdir=outfolder, mode='total')
    pops_complex = POPS_parse2(asa_data, mode='total') 
    complexWT_sasas.append(list(pops_complex.values()))

In [11]:
complexWT_sasas = np.asarray(complexWT_sasas)

In [12]:
sasa_WT_df = pd.DataFrame(complexWT_sasas,columns=["sasa_phil_wt","sasa_phob_wt","sasa_wt"],index=[pdb.name for pdb in repairedWT_pdbs])

In [13]:
sasa_WT_df

sasa_phil_wt  sasa_phob_wt   sasa_wt
1AHW_Repair.pdb      15279.74      46567.53  61847.27
1DVF_Repair.pdb       5763.77      15080.17  20843.95
1JRH_Repair.pdb       7407.09      16501.38  23908.47
1VFB_Repair.pdb       4676.71      12160.92  16837.63
3HFM_Repair.pdb       6993.79      20082.62  27076.41

## merge data sasa wt and mut

In [14]:
interface_asa_MUT_df = pd.read_csv("benedix_sasa_mut.v2.csv",index_col=0)

In [15]:
interface_mut_index_code = interface_asa_MUT_df.index.str.split(".",expand=True).get_level_values(0)


In [16]:
# set new index equal to pdb code name
interface_asa_MUT_df['codes'] = interface_mut_index_code
interface_asa_MUT_df.reset_index(inplace=True)
interface_asa_MUT_df.set_index('codes',inplace=True)

# set new index equal to pdb code name
sasa_WT_df['codes'] = sasa_WT_df.index.str[:-11]
sasa_WT_df.reset_index(inplace=True)
sasa_WT_df.set_index('codes',inplace=True)

In [351]:
# Drop useless columns
DF_sasa_wt_mut = interface_asa_MUT_df.merge(sasa_WT_df,on='codes')
DF_sasa_wt_mut = DF_sasa_wt_mut.set_index("index_x").drop("index_y",axis=1)
DF_sasa_wt_mut.index.name = None

In [352]:
DF_sasa_wt_mut.to_csv("benedix_SASA_data.v2.csv")

# DAta final

In [322]:
DF_energetic_changes = pd.read_csv("benedix_energetic_change_data.csv",index_col=0)

# Process
# Drop useless columns, set new index
DF_energetic_changes.reset_index(drop=True,inplace=True)
DF_energetic_changes.drop(["index_y",'number_of_residues_y'],axis=1,inplace=True)
DF_energetic_changes.set_index('index_x',inplace=True)
DF_energetic_changes.index.name = None

In [323]:
DF_sasa_wt_mut = pd.read_csv("benedix_SASA_data.csv",index_col=0)

In [324]:
# Merge contac and energetic data
contact_data = pd.read_csv("benedix_contact15_data.csv",index_col=0)

In [325]:
DF_contact_energy = contact_data.join(DF_energetic_changes)

In [326]:
# merge new data with sasa data
DF_contact_energy_sasa = DF_contact_energy.join(DF_sasa_wt_mut)

In [327]:
DF_contact_energy_sasa.to_csv("benedix_contact15_energetic_sasa.csv")

# load models SVR,RD and xgb

In [17]:
modelRF = joblib.load('RFmodel_contact15energy_sasa_Zero.pkl')
svrlinear = joblib.load('SVRmodel_contact400energy_sasa_linear.pkl')
svrrbf = joblib.load('SVRmodel_contact400energy_sasa_rbf.pkl')
ridgelinear = joblib.load('Ridgemodel_contact400energy_sasa_fCorr.pkl')
lassolinear = joblib.load('Lassomodel_contact400energy_sasa_fCorr.pkl')
elasticlinear = joblib.load('Elasticmodel_contact400energy_sasa_fCorr.pkl')


In [298]:
svrlinearPCA = joblib.load("SVRmodel_contact400energy_sasa_linearPCA.pkl")
svrrbfPCA = joblib.load('SVRmodel_contact400energy_sasa_rbfPCA.pkl')


# prediction

In [7]:
# Load and proces data for prediction
DF_contact_energy_sasa = pd.read_csv("benedix_contact15_energetic_sasa.v2.csv",index_col=0)

In [8]:
# Preprocess data

with open('cols_selected_zero15.pickle', 'rb') as f:
    # The protocol version used is detected automatically, so we do not
    # have to specify it.
    cols_selected_zero = pickle.load(f)

In [ ]:
with open('drop_correlated.pickle', 'rb') as f:
    # The protocol version used is detected automatically, so we do not
    # have to specify it.
    drop_correlated = pickle.load(f)


In [13]:
DF_contact_energy_sasa_f1 = DF_contact_energy_sasa.loc[:, cols_selected_zero]
DF_contact_energy_sasa_f1.drop("ddG_exp",axis=1,inplace=True)
#DF_contact_energy_sasa_f2 = DF_contact_energy_sasa_f1.drop(drop_correlated,axis=1)

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/pandas/core/indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)


In [204]:
#DF_contact_energy_sasa_f2.drop("ddG_exp",axis=1,inplace=True)

In [18]:
#svrlinear_pred = svrlinear.predict(DF_contact_energy_sasa_f2.values)
#svrrbf_pred = svrrbf.predict(DF_contact_energy_sasa_f2.values)
rf_pred = modelRF.predict(DF_contact_energy_sasa_f1)
#ridgelinear_pred = ridgelinear.predict(DF_contact_energy_sasa_f2.values)
#lassolinear_pred = lassolinear.predict(DF_contact_energy_sasa_f2.values)
#elasticlinear_pred = elasticlinear.predict(DF_contact_energy_sasa_f2.values)

In [212]:
pred_list = [svrlinear_pred,svrrbf_pred,rf_pred,ridgelinear_pred,lassolinear_pred,elasticlinear_pred]

In [223]:
corr_list = list()
for p in pred_list:
    corr = np.corrcoef(p,data_notin_modeldf['Experimental'])
    corr_list.append(corr[0,1])

In [231]:
np.column_stack(pred_list).mean(axis=1)

array([ 1.00991714,  0.88753756,  0.89129731,  1.09150189,  1.13086122,
        1.00353554,  1.00278702,  0.84237313,  1.08325591,  0.91155921,
        0.98793542,  1.01079566,  0.77500311,  1.20463898,  0.95574515,
        0.84861922,  0.96513566,  1.0133047 ,  1.02209477,  0.98724675,
        0.97590907,  1.00606604,  0.87046594, 16.67216285, 16.97649986,
       16.52152738, 16.53320753, 16.64592226, 16.73053205,  2.1915147 ,
        1.68969285,  2.01014024,  1.97848428,  2.35015353,  2.87337529,
        2.68271707,  2.76262601,  2.4834642 ,  2.76016337,  2.56122348,
        2.93436761,  2.63056647,  2.65721686,  2.64620684,  2.70292594,
        2.69169796,  2.61466373,  2.68259946,  2.53363499,  2.63493534,
        2.7391597 ,  2.59128858,  2.64853033,  2.60389419,  2.79733117,
        2.72680562,  2.49183588,  2.68489943,  2.70353408,  2.63722701,
        2.80394958,  2.52592729,  2.72654947])

In [47]:
data_notin_modeldf

Mutation type       PDB Mutation Chain  Predicted  Experimental  \
0        Original  1JRH.pdb     E27A     L     -2.021         -0.54   
1        Original  1JRH.pdb     D28A     L     -1.228         -0.44   
2        Original  1JRH.pdb     Y30A     L     -1.800         -1.10   
3        Original  1JRH.pdb     K47A     I     -0.309         -3.60   
4        Original  1JRH.pdb     Y32A     H      0.322         -1.40   
5        Original  1JRH.pdb     W53A     H      0.815         -2.40   
6        Original  1JRH.pdb     D54A     H     -0.229         -1.90   
7        Original  1JRH.pdb     D56A     H     -0.743         -1.80   
8        Original  1JRH.pdb     Y99A     H      0.000         -1.10   
9        Original  1JRH.pdb     N79A     I     -0.951          0.40   
10       Original  1JRH.pdb     W82A     I     -1.210         -4.50   
11       Original  1JRH.pdb     R84A     I     -0.664          0.30   
12       Original  1JRH.pdb     Y91A     L     -4.015         -0.58   
13       Original  1JRH.pdb     W92A     L     -4.121         -2.80   
14       Original  1JRH.pdb     K98A     I     -0.398          0.00   
15       Original  1JRH.pdb     W56F     I     -1.283          0.70   
25       Original  1VFB.pdb     H30A     A     -0.248         -0.80   
27       Original  1VFB.pdb     T30A     B     -0.571         -0.10   
29       Original  1VFB.pdb     T53A     A     -0.432          0.23   
31       Original  1VFB.pdb     R99A     B     -1.822         -0.10   
33       Original  1VFB.pdb     S93A     A     -1.175         -0.30   
34       Original  1VFB.pdb     Y50F     A     -0.932         -0.48   
35       Original  1VFB.pdb     Y32F     B     -0.432         -0.21   
36       Original  1AHW.pdb    Y157A     C     -1.316          1.90   
37       Original  1AHW.pdb    T167A     C     -1.280          0.00   
38       Original  1AHW.pdb    T170A     C      0.686         -1.00   
39       Original  1AHW.pdb    D178A     C     -0.833          0.50   
40       Original  1AHW.pdb    T197A     C     -0.563         -1.30   
41       Original  1AHW.pdb    V198A     C      0.140          0.30   
49       Original  1DVF.pdb    Y101A     B     -2.648         -2.00   
..            ...       ...      ...   ...        ...           ...   
65       Original  1DVF.pdb     Y98A     D     -3.717         -4.70   
71       Original  3HFM.pdb     W98A     H     -4.170         -5.50   
72       Original  3HFM.pdb     W98F     H     -1.873         -3.27   
83       Original  3HFM.pdb    S100A     Y     -2.310         -0.27   
84       Original  3HFM.pdb    D101A     Y     -0.055         -1.21   
85       Original  3HFM.pdb    D101N     Y      0.666         -1.34   
86       Original  3HFM.pdb    D101Q     Y      0.604         -1.92   
87       Original  3HFM.pdb    D101R     Y      0.318         -2.13   
88       Original  3HFM.pdb    D101S     Y      0.172         -1.71   
89       Original  3HFM.pdb     H15A     Y      0.136          0.45   
90       Original  3HFM.pdb     N19D     Y      0.520         -0.41   
91       Original  3HFM.pdb     N19K     Y      0.614         -0.23   
92       Original  3HFM.pdb     N19Q     Y      0.437          0.04   
94       Original  3HFM.pdb     Y20F     Y     -2.123          0.47   
95       Original  3HFM.pdb     Y20L     Y     -4.373         -2.20   
97       Original  3HFM.pdb     R21E     Y      0.167         -2.30   
98       Original  3HFM.pdb     R21H     Y     -0.402         -2.01   
99       Original  3HFM.pdb     R21K     Y     -0.326         -1.61   
100      Original  3HFM.pdb     R21M     Y     -0.008         -2.05   
101      Original  3HFM.pdb     R21N     Y      0.995         -2.17   
102      Original  3HFM.pdb     R21Q     Y      0.211         -2.24   
103      Original  3HFM.pdb     R21W     Y     -1.372         -1.97   
104      Original  3HFM.pdb     W63A     Y     -0.766         -0.32   
105      Original  3HFM.pdb     R73A     Y     -0.311          0.33   
106      Original  3HFM.pdb 

In [44]:
data_notin_modeldf= data_notin_modeldf.drop('Experimental')

In [46]:
np.corrcoef(data_notin_modeldf['Predicted'],data_notin_modeldf['Experimental'])

array([[1.        , 0.00159604],
       [0.00159604, 1.        ]])

In [128]:
y_true = data_notin_modeldf['Experimental']
y_pred = xgborder_pred

In [37]:
data_notin_modeldf.shape

(64, 8)

In [130]:
y_pred

array([0.16082844, 0.5899938 , 0.65092415, 0.44956222, 0.3435312 ,
       0.13491294, 0.5380964 , 0.5899938 , 0.5508399 , 0.7317958 ,
       0.4453377 , 0.13491294, 0.7522522 , 1.9011898 , 0.65277845,
       0.16082844, 0.50389034, 0.5752284 , 0.8197342 , 0.5359299 ,
       1.2382605 , 0.69847095, 0.87442017, 1.2504306 , 1.3019216 ,
       1.2881689 , 1.2504306 , 1.212352  , 1.2504108 , 2.4139466 ,
       1.9006171 , 1.8705094 , 2.3152595 , 4.502226  , 4.5952883 ,
       3.816199  , 3.527321  , 3.1244245 , 3.6281772 , 3.6330357 ,
       3.5702055 , 3.2317262 , 3.5971262 , 3.7613165 , 3.7674053 ,
       3.7674053 , 4.224478  , 3.4720302 , 2.2128525 , 2.2748556 ,
       2.2128525 , 2.1536512 , 2.2092943 , 2.2536836 , 2.3872993 ,
       3.4120321 , 3.3439026 , 2.1201353 , 2.7526717 , 3.1899524 ,
       4.7803044 , 3.3876905 , 4.0617385 ], dtype=float32)